# Attack on Firmware Implementation of AES (Acquisition + Visualization + DPA + CPA) based on CW code :-)

First you'll need to select which hardware setup you have. You'll need to select a `SCOPETYPE`, a `PLATFORM`, and a `CRYPTO_TARGET`. `SCOPETYPE` can either be `'OPENADC'` for the CWLite/CW1200 or `'CWNANO'` for the CWNano. `PLATFORM` is the target device, with `'CWLITEARM'`/`'CW308_STM32F3'` being the best supported option, followed by `'CWLITEXMEGA'`/`'CW308_XMEGA'`, then by `'CWNANO'`. `CRYPTO_TARGET` selects the crypto implementation, with `'TINYAES128C'` working on all platforms. An alternative for `'CWLITEXMEGA'` targets is `'AVRCRYPTOLIB'`. For example:

```python
SCOPETYPE = 'OPENADC'
PLATFORM = 'CWLITEARM'
CRYPTO_TARGET='TINYAES128C'
SS_VER='SS_VER_1_1'
```

In [ ]:
SCOPETYPE = 'OPENADC'
PLATFORM = 'CWNANO'
CRYPTO_TARGET='TINYAES128C'
SS_VER='SS_VER_1_1'

The following code will build the firmware for the target.

In [ ]:
%run "../../Setup_Scripts/Setup_Generic.ipynb"

In [ ]:
%%bash -s "$PLATFORM" "$CRYPTO_TARGET" "$SS_VER"
cd ../../../hardware/victims/firmware/simpleserial-aes
make PLATFORM=$1 CRYPTO_TARGET=$2 SS_VER=$3

In [ ]:
cw.program_target(scope, prog, "../../../hardware/victims/firmware/simpleserial-aes/simpleserial-aes-{}.hex".format(PLATFORM))

NANO is noisy, let's take 10000 :-D !

In [ ]:
from tqdm.notebook import trange
import numpy as np
import time

ktp = cw.ktp.Basic()
trace_array = []
textin_array = []

scope.adc.samples = 15000

key, text = ktp.next()

target.set_key(key)

N = 10000 #increase nano reliability
if PLATFORM=="CWNANO":
    N = 10000
for i in trange(N, desc='Capturing traces'):
    scope.arm()
    
    target.simpleserial_write('p', text)
    
    ret = scope.capture()
    if ret:
        print("Target timed out!")
        continue
    
    response = target.simpleserial_read('r', 16)
    
    trace_array.append(scope.get_last_trace())
    textin_array.append(text+response)
    
    key, text = ktp.next()
    
trace_array = np.array(trace_array)

We don't need the hardware anymore, so we'll disconnect:

In [ ]:
scope.dis()
target.dis()

### Plot the first and last trace using matplotlib. Use for example:
%matplotlib notebook

import matplotlib.pylab as plt

Also please print the input to the first trace and the key. 

In [ ]:
#implement it

## Different settings for acquistion

### Please experiment with different settings for acquision. 

Check:
https://chipwhisperer.readthedocs.io/en/latest/scope-api.html#api-scope-cwnano

Try modyfying: scope.adc.samples 

Read and print other settings of scope.adc 


## How to write and read traces and data?

In [ ]:
np_traces = np.asarray(trace_array)
np_textins = np.asarray(textin_array)
np.save('./traces.npy', np_traces)
np.save('./textins.npy', np_textins)

# Start from here!!!

## How to read traces and data?

In [ ]:
from tqdm.notebook import trange
import numpy as np
import time

%matplotlib notebook
import matplotlib.pylab as plt


#trace_array = np.load('./traces.npy') #modified name of the variable
#textin_array = np.load('./textins.npy') #modified name of the variable

#plot the traces that you read

plt.figure()
plt.plot(trace_array[0])
plt.plot(trace_array[999])
plt.xlabel("Time")
plt.ylabel("Values")
plt.title("Traces")
plt.legend()
plt.show()
print(textin_array[0])

hex_str = "2b 7e 15 16 28 ae d2 a6 ab f7 15 88 09 cf 4f 3c"
key = [int(x, base=16) for x in hex_str.split(' ')]
print([hex(i) for i in key])

## Helper code. What do you see below?

In [ ]:
# ###################
# START HELP
# ###################
sbox = [
    # 0    1    2    3    4    5    6    7    8    9    a    b    c    d    e    f
    0x63,0x7c,0x77,0x7b,0xf2,0x6b,0x6f,0xc5,0x30,0x01,0x67,0x2b,0xfe,0xd7,0xab,0x76, # 0
    0xca,0x82,0xc9,0x7d,0xfa,0x59,0x47,0xf0,0xad,0xd4,0xa2,0xaf,0x9c,0xa4,0x72,0xc0, # 1
    0xb7,0xfd,0x93,0x26,0x36,0x3f,0xf7,0xcc,0x34,0xa5,0xe5,0xf1,0x71,0xd8,0x31,0x15, # 2
    0x04,0xc7,0x23,0xc3,0x18,0x96,0x05,0x9a,0x07,0x12,0x80,0xe2,0xeb,0x27,0xb2,0x75, # 3
    0x09,0x83,0x2c,0x1a,0x1b,0x6e,0x5a,0xa0,0x52,0x3b,0xd6,0xb3,0x29,0xe3,0x2f,0x84, # 4
    0x53,0xd1,0x00,0xed,0x20,0xfc,0xb1,0x5b,0x6a,0xcb,0xbe,0x39,0x4a,0x4c,0x58,0xcf, # 5
    0xd0,0xef,0xaa,0xfb,0x43,0x4d,0x33,0x85,0x45,0xf9,0x02,0x7f,0x50,0x3c,0x9f,0xa8, # 6
    0x51,0xa3,0x40,0x8f,0x92,0x9d,0x38,0xf5,0xbc,0xb6,0xda,0x21,0x10,0xff,0xf3,0xd2, # 7
    0xcd,0x0c,0x13,0xec,0x5f,0x97,0x44,0x17,0xc4,0xa7,0x7e,0x3d,0x64,0x5d,0x19,0x73, # 8
    0x60,0x81,0x4f,0xdc,0x22,0x2a,0x90,0x88,0x46,0xee,0xb8,0x14,0xde,0x5e,0x0b,0xdb, # 9
    0xe0,0x32,0x3a,0x0a,0x49,0x06,0x24,0x5c,0xc2,0xd3,0xac,0x62,0x91,0x95,0xe4,0x79, # a
    0xe7,0xc8,0x37,0x6d,0x8d,0xd5,0x4e,0xa9,0x6c,0x56,0xf4,0xea,0x65,0x7a,0xae,0x08, # b
    0xba,0x78,0x25,0x2e,0x1c,0xa6,0xb4,0xc6,0xe8,0xdd,0x74,0x1f,0x4b,0xbd,0x8b,0x8a, # c
    0x70,0x3e,0xb5,0x66,0x48,0x03,0xf6,0x0e,0x61,0x35,0x57,0xb9,0x86,0xc1,0x1d,0x9e, # d
    0xe1,0xf8,0x98,0x11,0x69,0xd9,0x8e,0x94,0x9b,0x1e,0x87,0xe9,0xce,0x55,0x28,0xdf, # e
    0x8c,0xa1,0x89,0x0d,0xbf,0xe6,0x42,0x68,0x41,0x99,0x2d,0x0f,0xb0,0x54,0xbb,0x16  # f
]

def aes_internal(inputdata, key):
    return sbox[inputdata ^ key]

HW = [bin(n).count("1") for n in range(0, 256)]

assert HW[aes_internal(0xA1, 0x79)] == 3
assert HW[aes_internal(0x22, 0xB1)] == 5
print("✔️ OK to continue!")

def mean(X):
    return np.sum(X, axis=0)/len(X)

def std_dev(X, X_bar):
    return np.sqrt(np.sum((X-X_bar)**2, axis=0))

def cov(X, X_bar, Y, Y_bar):
    return np.sum((X-X_bar)*(Y-Y_bar), axis=0)
# ###################
# END HELP
# ###################

## Implement DPA for one input bit. Plot the result. What do you see?

In [ ]:
# ###################
# START SOLUTION
# ##########guessed_byte#########
import numpy as np
mean_diffs = np.zeros(256)

one_list = []
zero_list = []
guessed_byte = 0

numtraces = 1000
   
for trace_index in range(numtraces):

    #Get a hypothetical leakage list - use aes_internal(guess, input_byte)
    hypothetical_leakage = textin_array[trace_index][guessed_byte]

    #Mask off the lowest bit - is it 0 or 1? Depending on that add trace to array
    if hypothetical_leakage & 0x80:
        one_list.append(trace_array[trace_index])
    else:
        zero_list.append(trace_array[trace_index])

one_avg = np.asarray(one_list).mean(axis=0)
zero_avg = np.asarray(zero_list).mean(axis=0)
difference = np.subtract(one_avg,zero_avg)

#Plot the difference!

%matplotlib notebook
import matplotlib.pylab as plt

plt.figure()
#plt.plot(one_avg)
#plt.plot(zero_avg)
plt.plot(difference)
plt.xlabel("Time")
plt.ylabel("Values")
plt.title("Traces")
plt.legend()
plt.show()

# ###################
# END SOLUTION
# ###################

## Implement DPA for one key byte using the most significant bit of the sbox output in round 1. 

In [ ]:
# ###################
# START SOLUTION
# ##########guessed_byte#########

import numpy as np
mean_diffs = np.zeros(256)

guessed_byte = 0

for guess in range(0, 256):

    one_list = []
    zero_list = []

    numtraces = 2000
    
    for trace_index in range(numtraces):

        #Get a hypothetical leakage list - use aes_internal(guess, input_byte)
        hypothetical_leakage = aes_internal(guess, textin_array[trace_index][guessed_byte])

        #Mask off the lowest bit - is it 0 or 1? Depending on that add trace to array
        if hypothetical_leakage & 0x80:
            one_list.append(trace_array[trace_index])
        else:
            zero_list.append(trace_array[trace_index])

    one_avg = np.asarray(one_list).mean(axis=0)
    zero_avg = np.asarray(zero_list).mean(axis=0)
    mean_diffs[guess] = np.max(abs(one_avg - zero_avg))

    print("Guessing %02x: %f"%(guess, mean_diffs[guess]))

maxdiff = max(mean_diffs)
indmax = np.argmax(mean_diffs)
#print(mean_diffs)

print("Best Key Guess: ", end="")
print("%02x, difference: %f" % (indmax, maxdiff), end="")
print("\n")
print("Real Key Guess: ", end="")
print("%02x, difference: %f" % (key[guessed_byte], mean_diffs[[key[guessed_byte]]]), end="")
print("\n")
print("Position: %d" % (mean_diffs>mean_diffs[[key[guessed_byte]]]).sum())

# ###################
# END SOLUTION
# ###################

## Can we recover all bytes with CPA using 100 traces?

In [ ]:
num=100
trace_array3=trace_array[0:num]
textin_array3=textin_array[0:num]

t_bar = np.sum(trace_array3, axis=0)/len(trace_array3)
o_t = np.sqrt(np.sum((trace_array3 - t_bar)**2, axis=0))

cparefs = [0] * 16 #put your key byte guess correlations here
bestguess = [0] * 16 #put your key byte guesses here

for bnum in range(0, 16):
    maxcpa = [0] * 256
    for kguess in range(0, 256):
    # ###################
    # Add your code here
    # ###################
    #raise NotImplementedError("Add your code here, and delete this.")

    # ###################
    # START SOLUTION
    # ###################
        hws = np.array([[HW[aes_internal(textin[bnum],kguess)] for textin in textin_array3]]).transpose()
        hws_bar = mean(hws)
        o_hws = std_dev(hws, hws_bar)
        correlation = cov(trace_array3, t_bar, hws, hws_bar)
        cpaoutput = correlation/(o_t*o_hws)
        maxcpa[kguess] = max(abs(cpaoutput))
    bestguess[bnum] = np.argmax(maxcpa)
    cparefs[bnum] = max(maxcpa)
    # ###################
    # END SOLUTION
    # ###################

print("Best Key Guess: ", end="")
for b in bestguess: print("%02x " % b, end="")
print("\n", cparefs)